In [99]:
# Initial imports
import pandas as pd
import hvplot.pandas
from path import Path
import plotly.express as px
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.preprocessing import LabelEncoder

In [141]:
# Load the newHH.csv dataset.
file = "Resources/newHH.csv"
HealthData_df = pd.read_csv(file, index_col=0)
HealthData_df.head()

HeartDisease    BMI Smoking AlcoholDrinking Stroke  PhysicalHealth  \
ID                                                                      
0            No  16.60     Yes              No     No             3.0   
1            No  20.34      No              No    Yes             0.0   
2            No  26.58     Yes              No     No            20.0   
3            No  24.21      No              No     No             0.0   
4            No  23.71      No              No     No            28.0   

    MentalHealth DiffWalking     Sex  AgeCategory   Race Diabetic  \
ID                                                                  
0           30.0          No  Female        55-59  White      Yes   
1            0.0          No  Female  80 or older  White       No   
2           30.0          No    Male        65-69  White      Yes   
3            0.0          No  Female        75-79  White       No   
4            0.0         Yes  Female        40-44  White       No   

   PhysicalActivity  GenHealth  SleepTime Asthma KidneyDisease SkinCancer  
ID                                                                         
0               Yes  Very good        5.0    Yes            No        Yes  
1               Yes  Very good        7.0     No            No         No  
2               Yes       Fair        8.0    Yes            No         No  
3                No       Good        6.0     No            No        Yes  
4               Yes  Very good        8.0     No            No         No

In [142]:
# Replacing "Yes" with 1 and "No" with 0

for i in HealthData_df.columns:
    if i != "Diabetic":
        HealthData_df[i] = HealthData_df[i].replace('Yes', 1)
        HealthData_df[i] = HealthData_df[i].replace('No', 0)
        
HealthData_df.head()


HeartDisease    BMI  Smoking  AlcoholDrinking  Stroke  PhysicalHealth  \
ID                                                                          
0              0  16.60        1                0       0             3.0   
1              0  20.34        0                0       1             0.0   
2              0  26.58        1                0       0            20.0   
3              0  24.21        0                0       0             0.0   
4              0  23.71        0                0       0            28.0   

    MentalHealth  DiffWalking     Sex  AgeCategory   Race Diabetic  \
ID                                                                   
0           30.0            0  Female        55-59  White      Yes   
1            0.0            0  Female  80 or older  White       No   
2           30.0            0    Male        65-69  White      Yes   
3            0.0            0  Female        75-79  White       No   
4            0.0            1  Female        40-44  White       No   

    PhysicalActivity  GenHealth  SleepTime  Asthma  KidneyDisease  SkinCancer  
ID                                                                             
0                  1  Very good        5.0       1              0           1  
1                  1  Very good        7.0       0              0           0  
2                  1       Fair        8.0       1              0           0  
3                  0       Good        6.0       0              0           1  
4                  1  Very good        8.0       0              0           0

In [143]:
# Encode Age, Sex, Race and Diabetic 
le = LabelEncoder()
HealthData_df['Sex'] = le.fit_transform(HealthData_df['Sex'])
HealthData_df['AgeCategory'] = le.fit_transform(HealthData_df['AgeCategory'])
#HealthData_df['Race'] = le.fit_transform(HealthData_df['Race'])
HealthData_df['GenHealth'] = le.fit_transform(HealthData_df['GenHealth'])
#HealthData_df['Diabetic'] = le.fit_transform(HealthData_df['Diabetic'])

In [144]:
#Get value counts for columns with object data type
for i in HealthData_df.columns:
    if HealthData_df[i].dtypes == object:
        print(HealthData_df[i].value_counts())

White                             245212
Hispanic                           27446
Black                              22939
Other                              10928
Asian                               8068
American Indian/Alaskan Native      5202
Name: Race, dtype: int64
No                          269653
Yes                          40802
No - Borderline diabetes      6781
Yes - During pregnancy        2559
Name: Diabetic, dtype: int64


In [145]:
#replacing object dtypes with string type
for i in HealthData_df.columns:
    if HealthData_df[i].dtypes == object:
        HealthData_df[i] = HealthData_df[i].astype("string")
        
#check dtypes

HealthData_df.dtypes

HeartDisease          int64
BMI                 float64
Smoking               int64
AlcoholDrinking       int64
Stroke                int64
PhysicalHealth      float64
MentalHealth        float64
DiffWalking           int64
Sex                   int32
AgeCategory           int32
Race                 string
Diabetic             string
PhysicalActivity      int64
GenHealth             int32
SleepTime           float64
Asthma                int64
KidneyDisease         int64
SkinCancer            int64
dtype: object

In [146]:
#Check counts with or without heartDisease
HealthData_df["HeartDisease"].value_counts()

0    292422
1     27373
Name: HeartDisease, dtype: int64

In [147]:
# Create a df for surveyors with HD
withdisease_df = HealthData_df.loc[HealthData_df['HeartDisease'] == 1]
withdisease_df['HeartDisease'].value_counts()

1    27373
Name: HeartDisease, dtype: int64

In [148]:
# Create a df for surveyors with no HD
nodisease_df = HealthData_df.loc[HealthData_df['HeartDisease'] == 0]
nodisease_df['HeartDisease'].value_counts()

0    292422
Name: HeartDisease, dtype: int64

In [149]:
# Remove the "HeartDisease" column. 
withdisease_df = withdisease_df.drop(columns=["HeartDisease"])
nodisease_df = nodisease_df.drop(columns=["HeartDisease"])


In [150]:
#Drop index columns
withdisease_df = withdisease_df.reset_index(drop=True)
nodisease_df = nodisease_df.reset_index(drop=True)
allcases_df = HealthData_df.reset_index(drop=True)

In [153]:
#Get Dummies for 'AgeCategory', 'Race', 'GenHealth', 'Diabetic' columns
X = withdisease_df
X = pd.get_dummies(X, columns=['Diabetic','Race']) 
X

BMI  Smoking  AlcoholDrinking  Stroke  PhysicalHealth  MentalHealth  \
0      28.87        1                0       0             6.0           0.0   
1      34.30        1                0       0            30.0           0.0   
2      32.98        1                0       1            10.0           0.0   
3      25.06        0                0       0             0.0           0.0   
4      30.23        1                0       0             6.0           2.0   
...      ...      ...              ...     ...             ...           ...   
27368  38.45        0                0       1            30.0          15.0   
27369  36.21        1                0       0             0.0           0.0   
27370  37.12        1                0       0             0.0           0.0   
27371  33.20        1                0       0             0.0           0.0   
27372  27.41        1                0       0             7.0           0.0   

       DiffWalking  Sex  AgeCategory  PhysicalActivity  ...  Diabetic_No  \
0                1    0           11                 0  ...            1   
1                1    1            8                 0  ...            0   
2                1    1           11                 1  ...            0   
3                1    0           12                 0  ...            0   
4                1    0           11                 1  ...            0   
...            ...  ...          ...               ...  ...          ...   
27368            1    0            7                 1  ...            0   
27369            1    0           11                 1  ...            0   
27370            0    1            3                 1  ...            1   
27371            0    0            8                 1  ...            0   
27372            1    1            8                 0  ...            0   

       Diabetic_No - Borderline diabetes  Diabetic_Yes  \
0                                      0             0   
1                                      0             1   
2                                      0             1   
3                                      0             1   
4                                      0             1   
...                                  ...           ...   
27368                                  0             1   
27369                                  0             1   
27370                                  0             0   
27371                                  0             1   
27372                                  0             1   

       Diabetic_Yes - During pregnancy  Race_American Indian/Alaskan Native  \
0                                    0                                    0   
1                                    0                                    0   
2                                    0                                    0   
3                                    0                                    0   
4                                    0                                    0   
...                                ...                                  ...   
27368                                0                                    0   
27369                                0                                    0   
27370                                0                                    0   
27371                                0                                    0   
27372                                0                                    0   

       Race_Asian  Race_Black  Race_Hispanic  Race_Other  Race_White  
0               0           1              0           0           0  
1               0           0              0           0           1  
2               0           0              0           0           1  
3               0           0              0           0           1  
4               0           0              0           0           1  
...           ...         ...            ...         ...       

In [155]:
# Standardize the data with StandardScaler().
scaled_df = StandardScaler().fit_transform(X)
scaled_df

array([[-0.08082554,  0.84075286, -0.20855813, ..., -0.23590215,
        -0.18289443, -2.15066493],
       [ 0.74477499,  0.84075286, -0.20855813, ..., -0.23590215,
        -0.18289443,  0.46497248],
       [ 0.54407652,  0.84075286, -0.20855813, ..., -0.23590215,
        -0.18289443,  0.46497248],
       ...,
       [ 1.1735399 ,  0.84075286, -0.20855813, ...,  4.23904564,
        -0.18289443, -2.15066493],
       [ 0.57752626,  0.84075286, -0.20855813, ...,  4.23904564,
        -0.18289443, -2.15066493],
       [-0.30281022,  0.84075286, -0.20855813, ...,  4.23904564,
        -0.18289443, -2.15066493]])

**Reducing Data Dimensions Using PCA**

In [156]:
# Using PCA to reduce dimension to three principal components.
# Initialize PCA model
pca = PCA(n_components=3)
hd_pca = pca.fit_transform(scaled_df)
hd_pca

array([[ 1.02574389,  1.73717408, -0.05936966],
       [ 2.12624875, -2.1004291 ,  0.09352121],
       [ 1.00467162, -2.29481214, -0.65614447],
       ...,
       [-0.0149237 ,  3.70828707, -0.90796394],
       [ 1.8918278 ,  2.04803348, -2.15602634],
       [ 3.18208006,  1.52620457, -1.10279428]])

In [157]:
# Create a DataFrame with the three principal components.
df_hd_pca = pd.DataFrame(
    data=hd_pca, columns=["PC 1", "PC 2", "PC 3"], 
    index=X.index
)
df_hd_pca.head()

PC 1      PC 2      PC 3
0  1.025744  1.737174 -0.059370
1  2.126249 -2.100429  0.093521
2  1.004672 -2.294812 -0.656144
3  0.656063 -2.254264 -0.855342
4  1.495952 -1.987667 -0.856938

**Clustering Crytocurrencies Using K-Means**

In [158]:
# Create an elbow curve to find the best value for K.
inertia = []
k = list(range(1, 11))

# Calculate the inertia for the range of K values
for i in k:
    km = KMeans(n_clusters=i, random_state=0)
    km.fit(df_hd_pca)
    inertia.append(km.inertia_)

In [159]:
# Define a DataFrame to plot the Elbow Curve using hvPlot
elbow_data = {"k": k, "inertia": inertia}
df_elbow = pd.DataFrame(elbow_data)
df_elbow.hvplot.line(x="k", y="inertia", title="Elbow Curve", xticks=k)

:Curve   [k]   (inertia)

**Running K-Means with k=4**

In [160]:
# Initialize the K-Means model.
model = KMeans(n_clusters=4, random_state=0)

# Fit the model
model.fit(df_hd_pca)

# Predict clusters
predictions = model.predict(df_hd_pca)
predictions

array([3, 2, 2, ..., 3, 3, 3])

In [161]:
# Create a new DataFrame including predicted clusters and features.
df_hd_pca["class"] = model.labels_

In [162]:
# Concatentate the withdisease_df and pcs_df DataFrames on the same col
clustered_df = pd.concat([X, df_hd_pca], axis=1)
print(clustered_df.shape)
clustered_df.head()

(27373, 29)


BMI  Smoking  AlcoholDrinking  Stroke  PhysicalHealth  MentalHealth  \
0  28.87        1                0       0             6.0           0.0   
1  34.30        1                0       0            30.0           0.0   
2  32.98        1                0       1            10.0           0.0   
3  25.06        0                0       0             0.0           0.0   
4  30.23        1                0       0             6.0           2.0   

   DiffWalking  Sex  AgeCategory  PhysicalActivity  ...  \
0            1    0           11                 0  ...   
1            1    1            8                 0  ...   
2            1    1           11                 1  ...   
3            1    0           12                 0  ...   
4            1    0           11                 1  ...   

   Race_American Indian/Alaskan Native  Race_Asian  Race_Black  Race_Hispanic  \
0                                    0           0           1              0   
1                                    0           0           0              0   
2                                    0           0           0              0   
3                                    0           0           0              0   
4                                    0           0           0              0   

   Race_Other  Race_White      PC 1      PC 2      PC 3  class  
0           0           0  1.025744  1.737174 -0.059370      3  
1           0           1  2.126249 -2.100429  0.093521      2  
2           0           1  1.004672 -2.294812 -0.656144      2  
3           0           1  0.656063 -2.254264 -0.855342      2  
4           0           1  1.495952 -1.987667 -0.856938      2  

[5 rows x 29 columns]

In [165]:
# Creating a 3D-Scatter with the PCA data and the clusters
fig = px.scatter_3d(
    clustered_df,
    x="PC 1",
    y="PC 2",
    z="PC 3",
    color="class",
    symbol="class",
    width=800
)
fig.update_layout(legend=dict(x=0, y=1))
fig.show()

In [166]:
# Get a silhouette_score for the model
score = silhouette_score(df_hd_pca, predictions)
score


0.49673488886729

In [167]:
#Create a df for each cluster
zero_df = clustered_df.loc[clustered_df["class"] == 0]
one_df = clustered_df.loc[clustered_df["class"] == 1]
two_df = clustered_df.loc[clustered_df["class"] == 2]
three_df = clustered_df.loc[clustered_df["class"] == 3]

In [168]:
#Create a summary df for all clusters with HeartDisease
withHD_summary_df = pd.DataFrame(zero_df.mean(), columns = ["Cluster 0"])
withHD_summary_df["Cluster 1"] = one_df.mean()
withHD_summary_df["Cluster 2"] = two_df.mean()
withHD_summary_df["Cluster 3"] = three_df.mean()
withHD_summary_df

Cluster 0  Cluster 1  Cluster 2  \
BMI                                  27.473185  30.881327  31.178043   
Smoking                               0.548106   0.728507   0.595524   
AlcoholDrinking                       0.051006   0.054730   0.019664   
Stroke                                0.093569   0.285068   0.159233   
PhysicalHealth                        2.662317  21.212670   6.977618   
MentalHealth                          1.900290  13.245637   2.278657   
DiffWalking                           0.140225   0.839043   0.397122   
Sex                                   0.658820   0.391726   0.673861   
AgeCategory                           9.566530   8.808231   9.776819   
PhysicalActivity                      0.800324   0.292394   0.622542   
GenHealth                             2.330774   2.073906   2.059472   
SleepTime                             7.319345   6.656109   7.348042   
Asthma                                0.100819   0.358759   0.146603   
KidneyDisease                         0.053907   0.217410   0.191047   
SkinCancer                            0.217503   0.183366   0.226379   
Diabetic_No                           0.985073   0.725059   0.000639   
Diabetic_No - Borderline diabetes     0.012794   0.036630   0.046843   
Diabetic_Yes                          0.000000   0.230985   0.951559   
Diabetic_Yes - During pregnancy       0.002132   0.007326   0.000959   
Race_American Indian/Alaskan Native   0.000512   0.008619   0.001599   
Race_Asian                            0.000085   0.000215   0.000160   
Race_Black                            0.000085   0.003232   0.001599   
Race_Hispanic                         0.000171   0.003017   0.000480   
Race_Other                            0.000597   0.003232   0.001119   
Race_White                            0.998550   0.981685   0.995044   
PC 1                                 -1.495463   1.139376   0.748151   
PC 2                                  0.057008  -0.511163  -1.462082   
PC 3                                  0.239366   1.817848  -1.151344   
class                                 0.000000   1.000000   2.000000   

                                     Cluster 3  
BMI                                  30.375607  
Smoking                               0.527036  
AlcoholDrinking                       0.034925  
Stroke                                0.204713  
PhysicalHealth                        8.505996  
MentalHealth                          6.112771  
DiffWalking                           0.422049  
Sex                                   0.501157  
AgeCategory                           8.116979  
PhysicalActivity                      0.600673  
GenHealth                             1.986324  
SleepTime                             6.874185  
Asthma                                0.245950  
KidneyDisease                         0.130234  
SkinCancer                            0.034294  
Diabetic_No                           0.547233  
Diabetic_No - Borderline diabetes     0.037029  
Diabetic_Yes                          0.406691  
Diabetic_Yes - During pregnancy       0.009047  
Race_American Indian/Alaskan Native   0.102251  
Race_Asian                            0.055333  
Race_Black                            0.358300  
Race_Hispanic                         0.299600  
Race_Other                            0.180307  
Race_White                            0.004208  
PC 1                                  1.591686  
PC 2                                  2.282615  
PC 3                                 -0.850264  
class                                 3.000000